### Uk Road Traffic Data Exploration and Visualization

#### Key Definitions:

- **Annual Average Daily Flow (AADF):** The average over a full year of the number of vehicles passing a point in the road network each day.  


- **Vehicle kilometre/mile:** One vehicle multiplied by one kilometre/mile travelled (vehicle kilometres/miles are calculated by multiplying the AADF by the corresponding length of road). For example, one vehicle travelling one kilometre/mile a day for a year would be 365 vehicle kilometres/miles. This is sometimes referred to as the **volume of traffic.**

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [3]:
!pip install geopandas

     |████████████████████████████████| 1.0 MB 27.1 MB/s 
     |████████████████████████████████| 6.3 MB 34.3 MB/s 
     |████████████████████████████████| 16.7 MB 349 kB/s 


In [ ]:
# !pip install utm

In [4]:
# import utm
import math 
import calendar
import pandas as pd
import datetime
import os
import json
from urllib.request import urlopen
import urllib.request
import random
from pyproj import Proj
from pyproj import Transformer,transformer
import shapely.geometry

import geopandas as gpd
##from shapely.geometry import Point
# import warnings
# warnings.simplefilter(action='ignore', category=FutureWarning)

from plotly.subplots import make_subplots
import plotly.graph_objects as go
import pandas as pd
import numpy as np
import re
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

# plotly
##import chart_studio.plotly as py
import plotly.graph_objs as go
from plotly import tools
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)
import plotly.express as px
from IPython.display import HTML
import plotly.express as px

In [5]:
import plotly.io as pio
pio.renderers.default = "colab"

In [6]:
import warnings
warnings.filterwarnings("ignore")
# warnings.filterwarnings('ignore', message='.*initial implementation of Parquet.*')

In [7]:
os.getcwd()

'/content'

In [8]:
os.chdir('/content/drive/My Drive/uk_traffic_data_2020')

In [9]:
os.listdir()

['dft_traffic_counts_aadf.csv',
 'uk_shape_file',
 'uk_road_map.geojson',
 'ne_50m_rivers_lake_centerlines.zip',
 'assets',
 'df_uk_aadf.parquet.gzip',
 'road_geojson.csv',
 'road10_geojson.csv',
 'road50_geojson.csv',
 'road100_geojson.csv',
 'uk_traffic_volume.csv',
 'vehicle_traffic_volume.csv',
 'rd_category_agg.csv',
 'veh_rd_traffic_volume.csv',
 'rd_type_traffic_volume.csv',
 'uk_traffic_analysis.ipynb',
 'british-flag.png']

In [10]:
##TRAFFIC DATASETS ###
uk_traffic = pd.read_csv('dft_traffic_counts_aadf.csv')

In [11]:
#size of the df
uk_traffic.shape

(489159, 33)

In [12]:
uk_traffic.year.unique()

array([2019, 2018, 2020, 2014, 2017, 2015, 2016, 2011, 2001, 2009, 2010,
       2013, 2008, 2007, 2006, 2005, 2004, 2003, 2002, 2012, 2000])

In [13]:
#check for missing values
uk_traffic.isnull().sum()

id                                   0
count_point_id                       0
year                                 0
region_id                            0
local_authority_id                   0
road_name                            0
road_category                        0
road_type                            0
start_junction_road_name        113133
end_junction_road_name          113124
easting                              0
northing                             0
latitude                             0
longitude                            0
link_length_km                  112767
link_length_miles               112767
sequence                        112767
ramp                            362461
estimation_method                    0
estimation_method_detailed           0
pedal_cycles                         0
two_wheeled_motor_vehicles           0
cars_and_taxis                       0
buses_and_coaches                    0
lgvs                                 0
hgvs_2_rigid_axle        

In [ ]:
# uk_traffic[["start_junction_road_name", "end_junction_road_name", "link_length_km", "link_length_miles", "sequence", "ramp"]]

In [14]:
##lets drop the four columns with the most missing values
uk_traffic = uk_traffic.drop(['start_junction_road_name', 'end_junction_road_name', "ramp", "sequence"], axis=1)

In [15]:
uk_traffic.dropna(inplace = True)

In [16]:
uk_traffic.shape

(376392, 29)

In [17]:
uk_traffic.year.unique()

array([2019, 2018, 2020, 2014, 2017, 2015, 2016, 2011, 2009, 2008, 2007,
       2006, 2005, 2004, 2003, 2002, 2001, 2012, 2000, 2013, 2010])

In [18]:
region_id = sorted(uk_traffic.region_id.unique().tolist())

In [19]:
region_name = ["South West", "East Midlands", "Scotland", "Wales", "North West", "London",
               "East of England", "Yorkshire & Humber", "South East", "West Midlands",
               "North East"]

In [20]:
uk_traffic['region_name'] = uk_traffic['region_id'].replace(region_id,region_name)

In [21]:
uk_traffic["all_vehicles"] = uk_traffic.apply(lambda x: (x['all_hgvs'] + x['all_motor_vehicles'] + x['pedal_cycles']), axis=1)

In [22]:
columns = uk_traffic.columns.tolist()

In [23]:
###calculate miles driven, the miles driven per year by a vehicle == Volume of traffic for that particular vehicle on a road
vehicles = ['pedal_cycles', 'two_wheeled_motor_vehicles', 'cars_and_taxis', 'buses_and_coaches', 'lgvs', 
            'hgvs_2_rigid_axle', 'hgvs_3_rigid_axle', 
            'hgvs_3_or_4_articulated_axle', 'hgvs_4_or_more_rigid_axle', 
            'hgvs_5_articulated_axle', 'hgvs_6_articulated_axle', 'all_hgvs', 'all_motor_vehicles', "all_vehicles"]

In [24]:
cols_without_vehicles = [col for col in columns if col not in vehicles]

In [25]:
##make a single column for all vehicles
uk_traffic = uk_traffic.melt(id_vars = cols_without_vehicles, 
                value_vars = vehicles,
                var_name = "vehicles",
                value_name = "vehicles_aadf")

In [26]:
vehs_values = uk_traffic.vehicles.unique().tolist()

In [27]:
vehs = ["Pedal Cycles", "Motor Cycles", "Cars and Taxis", "Buses and Coaches", "Lorries and Vans", "2 rigid axle HGV",
        "3 rigid axle HGV", "3/4 rigid axle HGV", "4 rigid axle HGV", "5 articulated axle HGV", "6 articulated axle HGV",
        "Heavy Goods Vehicles", "Motor vehicles", "All vehicles"
        ]

In [28]:
uk_traffic['vehicles'] = uk_traffic['vehicles'].replace(vehs_values,vehs)

In [29]:
uk_traffic["vehicles_miles_driven"] = uk_traffic.apply(lambda x: (x['link_length_miles'] * x['vehicles_aadf'] * 365), axis=1)

In [30]:
uk_traffic.head()

id  count_point_id  year  region_id  local_authority_id road_name  \
0   1           27294  2019          5                  85      A560   
1   2            1153  2019          3                  30      A905   
2   3            8024  2019          9                  80       M20   
3   4           20505  2019          4                   6    A48(M)   
4   5           46628  2019          5                 162       A62   

  road_category road_type  easting  northing   latitude  longitude  \
0            PA     Major   380000    389400  53.401041  -2.302268   
1            PA     Major   292310    680000  56.000814  -3.728354   
2            TM     Major   561000    159600  51.312739   0.308688   
3            TM     Major   325000    183640  51.546649  -3.082974   
4            PA     Major   392080    404710  53.538976  -2.120975   

   link_length_km  link_length_miles estimation_method  \
0             2.8               1.74         Estimated   
1             1.1               0.68           Counted   
2             2.1               1.30         Estimated   
3             2.8               1.74         Estimated   
4             0.5               0.31           Counted   

                          estimation_method_detailed region_name  \
0  Estimated using previous year's AADF on this link  North West   
1                                       Manual count    Scotland   
2  Estimated using previous year's AADF on this link  South East   
3  Estimated using previous year's AADF on this link       Wales   
4                                       Manual count  North West   

       vehicles  vehicles_aadf  vehicles_miles_driven  
0  Pedal Cycles            214               135911.4  
1  Pedal Cycles              2                  496.4  
2  Pedal Cycles              0                    0.0  
3  Pedal Cycles              0                    0.0  
4  Pedal Cycles              0                    0.0

In [31]:
uk_traffic['road_category'].value_counts()

PA    4269594
TA     670824
TM     317912
PM      11158
Name: road_category, dtype: int64

In [32]:
len(uk_traffic.road_name.unique().tolist())

1879

In [33]:
rd_category = uk_traffic.road_category.unique().tolist()

In [34]:
road_category_description = ['Class A Principal Road', 'M or Class A Trunk Motorway', 'Class A Trunk Road', 
                             'M or Class A Principal Motorway']

In [35]:
uk_traffic['road_category'] = uk_traffic['road_category'].replace(rd_category,road_category_description)

In [36]:
uk_traffic['road_category'].value_counts()

Class A Principal Road             4269594
Class A Trunk Road                  670824
M or Class A Trunk Motorway         317912
M or Class A Principal Motorway      11158
Name: road_category, dtype: int64

In [37]:
uk_traffic = uk_traffic.loc[uk_traffic['northing']!=uk_traffic['northing'].max()]

In [38]:
uk_traffic.shape

(5269474, 20)

In [39]:
uk_traffic.columns

Index(['id', 'count_point_id', 'year', 'region_id', 'local_authority_id',
       'road_name', 'road_category', 'road_type', 'easting', 'northing',
       'latitude', 'longitude', 'link_length_km', 'link_length_miles',
       'estimation_method', 'estimation_method_detailed', 'region_name',
       'vehicles', 'vehicles_aadf', 'vehicles_miles_driven'],
      dtype='object')

In [46]:
len(uk_traffic[uk_traffic["year"] == 2008].road_name.unique())

1800

In [40]:
uk_traffic_volume = uk_traffic.groupby(["year","region_name", "vehicles"], as_index=False).agg(traffic_volume =("vehicles_miles_driven", sum))

In [ ]:
uk_traffic_volume.to_csv("uk_traffic_volume.csv", index=False)

In [ ]:
uk_traffic_volume.head()

year    region_name                vehicles  traffic_volume
0  2000  East Midlands        2 rigid axle HGV    5.890764e+08
1  2000  East Midlands        3 rigid axle HGV    7.811334e+07
2  2000  East Midlands      3/4 rigid axle HGV    1.910029e+08
3  2000  East Midlands        4 rigid axle HGV    8.234625e+07
4  2000  East Midlands  5 articulated axle HGV    4.700785e+08

In [ ]:
vehs

['Pedal Cycles',
 'Motor Cycles',
 'Cars and Taxis',
 'Buses and Coaches',
 'Lorries and Vans',
 '2 rigid axle HGV',
 '3 rigid axle HGV',
 '3/4 rigid axle HGV',
 '4 rigid axle HGV',
 '5 articulated axle HGV',
 '6 articulated axle HGV',
 'Heavy Goods Vehicles',
 'Motor vehicles',
 'All vehicles']

In [ ]:
colors = ['lightslategray', 'crimson', 'darkcyan', 'darkgoldenrod', 'cornsilk', 'turquoise', 'limegreen', \
              'darkorchid', 'palevioletred', 'forestgreen', 'silver', 'lightsteelblue']

In [ ]:
uk_traffic_volume

year         region_name                vehicles  traffic_volume
0     2000       East Midlands        2 rigid axle HGV    5.890764e+08
1     2000       East Midlands        3 rigid axle HGV    7.811334e+07
2     2000       East Midlands      3/4 rigid axle HGV    1.910029e+08
3     2000       East Midlands        4 rigid axle HGV    8.234625e+07
4     2000       East Midlands  5 articulated axle HGV    4.700785e+08
...    ...                 ...                     ...             ...
3229  2020  Yorkshire & Humber    Heavy Goods Vehicles    1.654965e+09
3230  2020  Yorkshire & Humber        Lorries and Vans    2.470936e+09
3231  2020  Yorkshire & Humber            Motor Cycles    6.382423e+07
3232  2020  Yorkshire & Humber          Motor vehicles    1.437583e+10
3233  2020  Yorkshire & Humber            Pedal Cycles    5.643242e+07

[3234 rows x 4 columns]

In [ ]:
sel_vehs = 'Lorries and Vans'

In [ ]:
sel_df = uk_traffic_volume[(uk_traffic_volume['vehicles'] == sel_vehs) & (uk_traffic_volume['region_name'].isin(region_name))].copy()

In [ ]:
fig = px.line(sel_df[(sel_df.year >= 2010)&(sel_df.year <= 2020)], x="year", y="traffic_volume", 
              color="region_name", color_discrete_sequence = colors, template="plotly_dark",
              markers=True, width=1400, height=800,)
fig.update_traces(textposition="bottom right")
fig.update_layout(
    title=f"<b> Volume of Traffic Trends for {sel_vehs}, 2000 - 2020 <b>",
    xaxis_title="Years",
    yaxis_title="Volume of Traffic",
    legend_title="Regions",
    font=dict(
        family="Courier New, monospace",
        size=18,
        color="white"
    )
)
fig.show()

In [ ]:
veh_traffic_volume = uk_traffic.groupby(["year", "vehicles"], as_index=False).agg(traffic_volume =("vehicles_miles_driven", sum))

In [ ]:
veh_traffic_volume.to_csv("vehicle_traffic_volume.csv", index=False)

In [ ]:
vehs

['Pedal Cycles',
 'Motor Cycles',
 'Cars and Taxis',
 'Buses and Coaches',
 'Lorries and Vans',
 '2 rigid axle HGV',
 '3 rigid axle HGV',
 '3/4 rigid axle HGV',
 '4 rigid axle HGV',
 '5 articulated axle HGV',
 '6 articulated axle HGV',
 'Heavy Goods Vehicles',
 'Motor vehicles',
 'All vehicles']

In [ ]:
fig = px.line(veh_traffic_volume[veh_traffic_volume["vehicles"] != "All vehicles"], x="year", y="traffic_volume", 
              color="vehicles", color_discrete_sequence = colors, template="plotly_dark",
              markers=True, width=1400, height=800,)
fig.update_traces(textposition="bottom right")
fig.show()

In [ ]:
# df_tips.groupby(["day","gender",'smoker'], as_index=False).agg(gender_count =("gender", count))

In [ ]:
colors = ['lightslategray',] * 21
colors[20] = 'crimson'

In [ ]:
# fig = px.bar(veh_traffic_volume[veh_traffic_volume["vehicles"] == "all_vehicles"], x= "year", y= "traffic_volume", color_discrete_sequence = colors,
#                  labels={'year':'<b> Years <b>'}, width=1000, height=650, 
#                  template="plotly_dark")
# fig.show()

In [ ]:
data = veh_traffic_volume[veh_traffic_volume["vehicles"] == "All vehicles"]

In [ ]:
fig = go.Figure()
fig.add_trace(go.Bar(x=data["year"], y=data["traffic_volume"],
                marker_color=colors))
fig.update_layout(title_text='Covid Impact on 2020 Road Traffic', width=1000, height=650, 
                 template="plotly_dark")

In [ ]:
#uk_traffic_volume[(uk_traffic_volume['vehicles'] == sel_vehs) & (uk_traffic_volume['region_name'].isin(region_name))]
colors = ['lightslategray',] * 21
colors[20] = 'crimson'

In [ ]:
dat_uk = uk_traffic_volume[(uk_traffic_volume['vehicles'] == sel_vehs) & (uk_traffic_volume['region_name'] == "London")]

In [ ]:
fig = go.Figure()
fig.add_trace(go.Bar(x=data["year"], y=data["traffic_volume"],
                marker_color=colors))
fig.update_layout(
    title_text='<b> Covid Impact on 2020 Road Traffic <b>',
    xaxis_title="Years",
    yaxis_title="Volume of Traffic",
    font=dict(
        family="Courier New, monospace",
        size=18,
        color="white"
    ),
  width=1200, height=700, 
  template="plotly_dark"
)
fig.show()

In [ ]:
traffic_2019_volume = veh_traffic_volume[veh_traffic_volume["year"] == 2019].reset_index(drop=True).copy()
traffic_2020_volume = veh_traffic_volume[veh_traffic_volume["year"] == 2020].reset_index(drop=True).copy()

In [ ]:
(traffic_2020_volume["traffic_volume"] - traffic_2019_volume["traffic_volume"]) / (traffic_2020_volume["traffic_volume"] + traffic_2019_volume["traffic_volume"])

0    -0.070077
1    -0.053017
2    -0.072695
3    -0.037965
4    -0.063997
5     0.012758
6    -0.128611
7    -0.231743
8    -0.163578
9    -0.035518
10   -0.056646
11   -0.174829
12   -0.136713
13    0.084486
Name: traffic_volume, dtype: float64

In [ ]:
traffic_2020_volume["volume_diff"] = (traffic_2020_volume["traffic_volume"] - traffic_2019_volume["traffic_volume"]) / (traffic_2020_volume["traffic_volume"] + traffic_2019_volume["traffic_volume"])

In [ ]:
traffic_2020_volume["volume_diff"] *= 100

In [ ]:
traffic_2020_volume

year                vehicles  traffic_volume  volume_diff
0   2020        2 rigid axle HGV    3.677966e+09    -7.007668
1   2020        3 rigid axle HGV    8.289675e+08    -5.301739
2   2020      3/4 rigid axle HGV    6.150656e+08    -7.269537
3   2020        4 rigid axle HGV    1.099690e+09    -3.796478
4   2020  5 articulated axle HGV    2.899251e+09    -6.399743
5   2020  6 articulated axle HGV    5.619017e+09     1.275810
6   2020            All vehicles    1.830667e+11   -12.861072
7   2020       Buses and Coaches    8.046864e+08   -23.174250
8   2020          Cars and Taxis    1.215034e+11   -16.357809
9   2020    Heavy Goods Vehicles    1.473971e+10    -3.551817
10  2020        Lorries and Vans    2.948932e+10    -5.664568
11  2020            Motor Cycles    1.026293e+09   -17.482925
12  2020          Motor vehicles    1.675634e+11   -13.671340
13  2020            Pedal Cycles    7.635662e+08     8.448587

In [ ]:
traffic_2020_volume.vehicles.unique().tolist()

['2 rigid axle HGV',
 '3 rigid axle HGV',
 '3/4 rigid axle HGV',
 '4 rigid axle HGV',
 '5 articulated axle HGV',
 '6 articulated axle HGV',
 'All vehicles',
 'Buses and Coaches',
 'Cars and Taxis',
 'Heavy Goods Vehicles',
 'Lorries and Vans',
 'Motor Cycles',
 'Motor vehicles',
 'Pedal Cycles']

In [ ]:
diff_color = ["steelblue" if val > 0 else "crimson" for val in traffic_2020_volume["volume_diff"]]

In [ ]:
diff_color

['crimson',
 'crimson',
 'crimson',
 'crimson',
 'crimson',
 'steelblue',
 'crimson',
 'crimson',
 'crimson',
 'crimson',
 'crimson',
 'crimson',
 'crimson',
 'steelblue']

In [ ]:
fig = go.Figure()
fig.add_trace(go.Bar(x=traffic_2020_volume["vehicles"], y=traffic_2020_volume["volume_diff"],
                     marker_color= diff_color))
fig.update_layout(
    title_text='<b> Change in miles travelled in UK, 2019-2020 <b>',
    xaxis_title="",
    yaxis_title="Percent Change %",
    font=dict(
        family="Courier New, monospace",
        size=18,
        color="white"
    ),
  width=1000, height=600, 
  template="plotly_dark"
)

In [ ]:
uk_traffic["road_category"].unique()

array(['Class A Principal Road', 'M or Class A Trunk Motorway',
       'Class A Trunk Road', 'M or Class A Principal Motorway'],
      dtype=object)

In [ ]:
rd_category_agg = uk_traffic.groupby(["year", "road_category"], as_index=False).agg(traffic_volume =("vehicles_miles_driven", sum))

In [ ]:
rd_category_agg.to_csv("rd_category_agg.csv", index=False)

In [ ]:
rd_2019_volume = rd_category_agg[rd_category_agg["year"] == 2019].reset_index(drop=True).copy()
rd_2020_volume = rd_category_agg[rd_category_agg["year"] == 2020].reset_index(drop=True).copy()

In [ ]:
rd_2020_volume["volume_diff"] = (rd_2020_volume["traffic_volume"] - rd_2019_volume["traffic_volume"]) / (rd_2020_volume["traffic_volume"] + rd_2019_volume["traffic_volume"]) * 100

In [ ]:
diff_color = ["steelblue" if val > 0 else "crimson" for val in rd_2020_volume["volume_diff"]]

In [ ]:
fig = go.Figure()
fig.add_trace(go.Bar(x=rd_2020_volume["road_category"], y=rd_2020_volume["volume_diff"],
                     marker_color= diff_color))

fig.update_layout(
    title_text='<b> Percent change in miles travelled in UK, 2010-2019 <b>',
    xaxis_title="",
    yaxis_title="Percent Change %",
    font=dict(
        family="Courier New, monospace",
        size=16,
        color="white"
    ),
  width=1100, height=600, 
  template="plotly_dark"
)

In [ ]:
veh_rd_traffic_volume = uk_traffic.groupby(["year", "vehicles", "road_category"], as_index=False).agg(traffic_volume =("vehicles_miles_driven", sum))

In [ ]:
veh_rd_traffic_volume.to_csv("veh_rd_traffic_volume.csv", index=False)

In [ ]:
veh_rd_traffic_volume

year          vehicles                    road_category  traffic_volume
0     2000  2 rigid axle HGV           Class A Principal Road    1.925270e+09
1     2000  2 rigid axle HGV               Class A Trunk Road    1.625332e+09
2     2000  2 rigid axle HGV  M or Class A Principal Motorway    1.274431e+07
3     2000  2 rigid axle HGV      M or Class A Trunk Motorway    2.054377e+09
4     2000  3 rigid axle HGV           Class A Principal Road    3.127989e+08
...    ...               ...                              ...             ...
1171  2020    Motor vehicles      M or Class A Trunk Motorway    5.202751e+10
1172  2020      Pedal Cycles           Class A Principal Road    7.448153e+08
1173  2020      Pedal Cycles               Class A Trunk Road    1.875092e+07
1174  2020      Pedal Cycles  M or Class A Principal Motorway    0.000000e+00
1175  2020      Pedal Cycles      M or Class A Trunk Motorway    0.000000e+00

[1176 rows x 4 columns]

In [ ]:
sel_vehicle = 'Cars and Taxis'
sel_year = 2020

In [ ]:
rd_data = veh_rd_traffic_volume[(veh_rd_traffic_volume["vehicles"] == sel_vehicle) & (veh_rd_traffic_volume["year"] == sel_year)]

In [ ]:
rd_data

year        vehicles                    road_category  traffic_volume
1152  2020  Cars and Taxis           Class A Principal Road    6.296429e+10
1153  2020  Cars and Taxis               Class A Trunk Road    2.395154e+10
1154  2020  Cars and Taxis  M or Class A Principal Motorway    3.987034e+08
1155  2020  Cars and Taxis      M or Class A Trunk Motorway    3.418889e+10

In [ ]:
miles_text = f"{(round(rd_data.traffic_volume.sum())//1000000000)} Billion Miles" if (round(rd_data.traffic_volume.sum())//1000000000) \
else f"{(round(rd_data.traffic_volume.sum())//1000000)} Million miles"

In [ ]:
billion = 1000000000
million = 1000000

In [ ]:
pie_color = ['lightslategray', 'cornsilk', 'turquoise', 'crimson'] #'cornsilk', 'turquoise', 'limegreen', \ 'crimson', 'darkcyan', 'darkgoldenrod'
              # 'darkorchid', 'palevioletred', 'forestgreen', 'silver', 'lightsteelblue'
fig = go.Figure()
fig.add_trace(go.Pie(labels=rd_data["road_category"], 
                     values=rd_data["traffic_volume"], 
                     marker_colors=pie_color,
                     name="Miles Driven"))

# Use `hole` to create a donut-like pie chart
fig.update_traces(hole=.55, hoverinfo="label+percent+name")

fig.update_layout(
    # Add annotations in the center of the donut pies.
    annotations=[dict(text=miles_text, x=0.50, y=0.58, font_size=20, showarrow=False),
                 dict(text=f'Covered in {sel_year}', x=0.50, y=0.53, font_size=20, showarrow=False),
                 dict(text=f'by {sel_vehicle}', x=0.50, y=0.48, font_size=20, showarrow=False)],
    template="plotly_dark", width=1200, height=650)
fig.update_layout(
    title_text=f'<b> Volume of Traffic by Vehicle Type & Year across major road types,{sel_year} <b>',
    font=dict(
        family="Courier New, monospace",
        size=16,
        color="white"
    ),
)
fig.show()

In [ ]:
rd_type_traffic_volume = uk_traffic.groupby(["year", "vehicles", "road_name"], as_index=False).agg(traffic_volume =("vehicles_miles_driven", sum))

In [ ]:
busiest_roads = ['M1', 'M6', 'M4', 'M25', 'A1', 'M5', 'M62', 'M40', 'A38', 'A14']

In [ ]:
rd_type_traffic_volume = rd_type_traffic_volume[rd_type_traffic_volume.road_name.isin(busiest_roads)].reset_index(drop=True)

In [ ]:
rd_type_traffic_volume.road_name.unique()

array(['A1', 'A14', 'A38', 'M1', 'M25', 'M4', 'M40', 'M5', 'M6', 'M62'],
      dtype=object)

In [ ]:
rd_type_traffic_volume.to_csv("rd_type_traffic_volume.csv", index=False)

In [ ]:
# rd_type_traffic_volume.sort_values(by=['traffic_volume'], ascending=False).head(10).road_name.values.tolist()

['M1', 'M1', 'M6', 'M6', 'M1', 'M6', 'M6', 'M1', 'M6', 'M6']

In [ ]:
sel_vh = "Motor vehicles"

In [ ]:
rd_name_data = rd_type_traffic_volume[(rd_type_traffic_volume["vehicles"] == sel_vh) & (rd_type_traffic_volume["year"] == 2020)]

In [ ]:
rd_name_data.sort_values(by=['traffic_volume'], ascending=False, inplace=True)

In [ ]:
fig = px.bar(rd_name_data, x= "traffic_volume", y= "road_name", color='road_name', orientation = 'h', 
             pattern_shape="road_name", pattern_shape_sequence=[".", "x", "+",".", '/', '\\', 'x', '-', '|', "+","."],
                 labels={'year':'<b> Years <b>'}, template="plotly_dark",
                 color_discrete_sequence = px.colors.sequential.YlOrRd_r)

fig.update_layout(
    title_text=f'<b> Volume of Traffic across Major Roads, {2020} ({sel_vh}) <b>',
    xaxis_title="Volume of Traffic",
    yaxis_title="Major Roads",
    font=dict(
        family="Courier New, monospace",
        size=18,
        color="white"
    ),
  width=1200, height=700, 
  template="plotly_dark",
  showlegend=False
)

In [ ]:
# fig = px.line(veh_traffic_volume[veh_traffic_volume["vehicles"] != "all_vehicles"], x="year", y="traffic_volume", 
#               color="vehicles", color_discrete_sequence = colors, template="plotly_dark",
#               markers=True, width=1400, height=800,)
# fig.update_traces(textposition="bottom right")
# fig.show()

#### Map Viz

In [ ]:
uk_topofile = "uk_shape_file/con_map.geojson"
uk_lad_json = "uk_shape_file/uk_lad_new.geojson"

In [ ]:
with open(uk_topofile) as f:
    data = json.load(f)

In [ ]:
uk_geojson = gpd.read_file(uk_topofile)

In [ ]:
uk_lad_geojson = gpd.read_file(uk_lad_json)

In [ ]:
with open(uk_lad_json) as f:
    lad_data = json.load(f)

In [ ]:
uk_lad_geojson.head(10)

id    LAD13CD LAD13CDO                      LAD13NM LAD13NMW  \
0  E06000001  E06000001     00EB                   Hartlepool     None   
1  E06000002  E06000002     00EC                Middlesbrough     None   
2  E06000003  E06000003     00EE         Redcar and Cleveland     None   
3  E06000004  E06000004     00EF             Stockton-on-Tees     None   
4  E06000005  E06000005     00EH                   Darlington     None   
5  E06000006  E06000006     00ET                       Halton     None   
6  E06000007  E06000007     00EU                   Warrington     None   
7  E06000008  E06000008     00EX        Blackburn with Darwen     None   
8  E06000009  E06000009     00EY                    Blackpool     None   
9  E06000010  E06000010     00FA  Kingston upon Hull, City of     None   

                                            geometry  
0  MULTIPOLYGON (((-1.24255 54.72217, -1.24151 54...  
1  MULTIPOLYGON (((-1.19777 54.58141, -1.19465 54...  
2  MULTIPOLYGON (((-1.20090 54.57811, -1.19986 54...  
3  MULTIPOLYGON (((-1.28213 54.56492, -1.27796 54...  
4  POLYGON ((-1.43834 54.59461, -1.43521 54.59571...  
5  MULTIPOLYGON (((-2.59533 53.32224, -2.59533 53...  
6  POLYGON ((-2.44953 53.41572, -2.45057 53.41462...  
7  POLYGON ((-2.46620 53.78082, -2.46203 53.77862...  
8  POLYGON ((-3.01085 53.82591, -3.01189 53.82591...  
9  MULTIPOLYGON (((-0.34799 53.77532, -0.34695 53...

In [ ]:
# uk_geojson['EER13CDO'] = uk_geojson['EER13CDO'].astype(int)

In [ ]:
# for feature,id in zip(data['features'],uk_geojson['EER13CDO']):
#   feature['id'] = id
#   print(feature['properties'])

In [ ]:
# for feature in lad_data['features']:
#   print(feature['properties'])

In [ ]:
laid = [1, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 4, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 3, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 208, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 5, 71, 72, 207, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 2, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 187, 188, 189, 190, 191, 192, 193, 194, 195, 196, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 58, 73, 148, 186]

In [ ]:
lad = ['Isles of Scilly', 'Newport', 'Bridgend', 'Swansea', 'Isle of Anglesey', 'Gwynedd', 'Conwy', 'Denbighshire', 'Monmouthshire', 'Powys', 'Carmarthenshire', 'Pembrokeshire', 'Neath Port Talbot', 'The Vale of Glamorgan', 'Cardiff', 'Flintshire', 'Merthyr Tydfil', 'Rhondda, Cynon, Taff', 'Ceredigion', 'Blaenau Gwent', 'Torfaen', 'Wrexham', 'West Lothian', 'Renfrewshire', 'City of Edinburgh', 'Falkirk', 'Perth & Kinross', 'Fife', 'Scottish Borders', 'East Lothian', 'North Lanarkshire', 'Highland', 'Midlothian', 'South Lanarkshire', 'Dumfries & Galloway', 'East Ayrshire', 'South Ayrshire', 'North Ayrshire', 'Stirling', 'West Dunbartonshire', 'Argyll & Bute', 'Aberdeenshire', 'Moray', 'Dundee City', 'Glasgow City', 'Inverclyde', 'East Dunbartonshire', 'Clackmannanshire', 'Aberdeen City', 'Angus', 'Comhairle nan Eilean Siar', 'Orkney Islands', 'Shetland Islands', 'Stockport', 'Barnet', 'Bedfordshire', 'Northamptonshire', 'Leicestershire', 'Derbyshire', 'Rotherham', 'Leeds', 'Medway', 'Hampshire', 'Hillingdon', 'West Berkshire', 'Wiltshire', 'Worcestershire', 'Gloucestershire', 'Somerset', 'Devon', 'Warwickshire', 'Cheshire', 'Warrington', 'Wigan', 'Lancashire', 'Cumbria', 'Hertfordshire', 'Doncaster', 'Kent', 'West Sussex', 'Portsmouth', 'Buckinghamshire', 'Wirral', 'Manchester', 'Bury', 'Calderdale', 'Wakefield', 'East Riding of Yorkshire', 'Salford', 'Trafford', 'Durham', 'Tower Hamlets', 'Sunderland', 'Rochdale', 'Islington', 'Cambridgeshire', 'Rutland', 'Lincolnshire', 'Nottinghamshire', 'North Yorkshire', 'Gateshead', 'Northumberland', 'Southwark', 'Lewisham', 'Greenwich', 'Bexley', 'Lambeth', 'Wandsworth', 'Westminster', 'Kensington and Chelsea', 'Hounslow', 'Slough', 'Wokingham', 'Reading', 'Bath and North East Somerset', 'Shropshire', 'Staffordshire', 'Brent', 'Derby', 'Luton', 'Enfield', 'Hackney', 'Essex', 'Redbridge', 'Waltham Forest', 'Suffolk', 'Southend-on-Sea', 'Thurrock', 'Peterborough', 'North Lincolnshire', 'North East Lincolnshire', 'Hartlepool', 'East Sussex', 'Croydon', 'Surrey', 'Brighton and Hove', 'Southampton', 'Dorset', 'Cornwall excluding Isles of Scilly', 'Stoke-on-Trent', 'Birmingham', 'Oxfordshire', 'South Gloucestershire', 'Bristol, City of', 'Camden', 'Hammersmith and Fulham', 'Ealing', 'Wolverhampton', 'Walsall', 'Solihull', 'Coventry', 'Leicester', 'Norfolk', 'Herefordshire, County of', 'Halton', 'Knowsley', 'St. Helens', 'Sheffield', 'Bolton', 'Liverpool', 'Oldham', 'Stockton-on-Tees', 'Darlington', 'Haringey', 'South Tyneside', 'Newham', 'Barking and Dagenham', 'Kingston upon Hull, City of', 'Middlesbrough', 'Redcar and Cleveland', 'Newcastle upon Tyne', 'North Tyneside', 'City of London', 'Richmond upon Thames', 'Bromley', 'Sutton', 'Kingston upon Thames', 'Windsor and Maidenhead', 'Bracknell Forest', 'Swindon', 'Bournemouth', 'North Somerset', 'Torbay', 'Harrow', 'Telford and Wrekin', 'Nottingham', 'Dudley', 'Sandwell', 'Milton Keynes', 'Sefton', 'Blackpool', 'Barnsley', 'Bradford', 'Tameside', 'Kirklees', 'Blackburn with Darwen', 'Isle of Wight', 'Poole', 'Havering', 'York', 'Plymouth', 'Merton', 'Caerphilly', 'East Renfrewshire', 'Central Bedfordshire', 'East Cheshire', 'West Cheshire', 'Bedford']

In [ ]:
lad_code = ['E06000053', 'W06000022', 'W06000013', 'W06000011', 'W06000001', 'W06000002', 'W06000003', 'W06000004', 'W06000021', 'W06000023', 'W06000010', 'W06000009', 'W06000012', 'W06000014', 'W06000015', 'W06000005', 'W06000024', 'W06000016', 'W06000008', 'W06000019', 'W06000020', 'W06000006', 'S12000040', 'S12000038', 'S12000036', 'S12000014', 'S12000048', 'S12000047', 'S12000026', 'S12000010', 'S12000044', 'S12000017', 'S12000019', 'S12000029', 'S12000006', 'S12000008', 'S12000028', 'S12000021', 'S12000030', 'S12000039', 'S12000035', 'S12000034', 'S12000020', 'S12000042', 'S12000046', 'S12000018', 'S12000045', 'S12000005', 'S12000033', 'S12000041', 'S12000013', 'S12000023', 'S12000027', 'E08000007', 'E09000003', 'E10000001', 'E10000021', 'E10000018', 'E10000007', 'E08000018', 'E08000035', 'E06000035', 'E10000014', 'E09000017', 'E06000037', 'E06000054', 'E10000034', 'E10000013', 'E10000027', 'E10000008', 'E10000031', 'E10000004', 'E06000007', 'E08000010', 'E10000017', 'E10000006', 'E10000015', 'E08000017', 'E10000016', 'E10000032', 'E06000044', 'E10000002', 'E08000015', 'E08000003', 'E08000002', 'E08000033', 'E08000036', 'E06000011', 'E08000006', 'E08000009', 'E06000047', 'E09000030', 'E08000024', 'E08000005', 'E09000019', 'E10000003', 'E06000017', 'E10000019', 'E10000024', 'E10000023', 'E08000037', 'E06000057', 'E09000028', 'E09000023', 'E09000011', 'E09000004', 'E09000022', 'E09000032', 'E09000033', 'E09000020', 'E09000018', 'E06000039', 'E06000041', 'E06000038', 'E06000022', 'E06000051', 'E10000028', 'E09000005', 'E06000015', 'E06000032', 'E09000010', 'E09000012', 'E10000012', 'E09000026', 'E09000031', 'E10000029', 'E06000033', 'E06000034', 'E06000031', 'E06000013', 'E06000012', 'E06000001', 'E10000011', 'E09000008', 'E10000030', 'E06000043', 'E06000045', 'E10000009', 'E06000052', 'E06000021', 'E08000025', 'E10000025', 'E06000025', 'E06000023', 'E09000007', 'E09000013', 'E09000009', 'E08000031', 'E08000030', 'E08000029', 'E08000026', 'E06000016', 'E10000020', 'E06000019', 'E06000006', 'E08000011', 'E08000013', 'E08000019', 'E08000001', 'E08000012', 'E08000004', 'E06000004', 'E06000005', 'E09000014', 'E08000023', 'E09000025', 'E09000002', 'E06000010', 'E06000002', 'E06000003', 'E08000021', 'E08000022', 'E09000001', 'E09000027', 'E09000006', 'E09000029', 'E09000021', 'E06000040', 'E06000036', 'E06000030', 'E06000028', 'E06000024', 'E06000027', 'E09000015', 'E06000020', 'E06000018', 'E08000027', 'E08000028', 'E06000042', 'E08000014', 'E06000009', 'E08000016', 'E08000032', 'E08000008', 'E08000034', 'E06000008', 'E06000046', 'E06000029', 'E09000016', 'E06000014', 'E06000026', 'E09000024', 'W06000018', 'S12000011', 'E06000056', 'E06000049', 'E06000050', 'E06000055']

In [ ]:
uk_traffic["local_authority_name"] = uk_traffic["local_authority_id"].replace(laid,lad)

In [ ]:
uk_traffic["local_authority_code"] = uk_traffic["local_authority_id"].replace(laid,lad_code)

In [ ]:
len(uk_lad_geojson["id"].unique().tolist())

380

In [ ]:
lad_not_found = [idx for idx in uk_lad_geojson["id"].unique().tolist() if idx not in lad_code]

In [ ]:
lad_not_found += [idx for idx in lad_code if idx not in uk_lad_geojson["id"].unique().tolist()]

In [ ]:
len(lad_not_found)

234

In [ ]:
random.sample(list(range(25,100)), 5)

[78, 68, 77, 49, 95]

In [ ]:
uk_lad_geojson.columns

Index(['id', 'LAD13CD', 'LAD13CDO', 'LAD13NM', 'LAD13NMW', 'geometry'], dtype='object')

In [ ]:
##aggreate volume of traffic by lad code
uk_lad_traffic_volume = uk_traffic.groupby(["year", "vehicles", "local_authority_code"], as_index=False).agg(traffic_volume =("vehicles_miles_driven", sum))

In [ ]:
uk_lad_geojson = uk_lad_geojson.rename({'LAD13CD': "local_authority_code"}, axis=1)

In [ ]:
uk_lad_geojson_agg =  pd.merge(uk_lad_geojson, uk_lad_traffic_volume, on="local_authority_code")

In [ ]:
uk_lad_not_fd = uk_lad_geojson[uk_lad_geojson["id"].isin(lad_not_found)].copy()

In [ ]:
len(uk_lad_geojson_agg.local_authority_code.unique())

177

##### Simulate volume of traffic for some lad

In [ ]:
def min_max_vehicles(df, veh_name):
  min_veh = df[df["vehicles"] == veh_name].traffic_volume.quantile(0.25)
  max_veh = df[df["vehicles"] == veh_name].traffic_volume.quantile(0.75)
  return min_veh, max_veh

In [ ]:
all_min_max_vals = [min_max_vehicles(uk_lad_geojson_agg, v) for v in vehs]

In [ ]:
uk_lad_geojson_agg[uk_lad_geojson_agg["vehicles"] == 'Pedal Cycles']["traffic_volume"].max()

23383334.45

In [ ]:
yrrs = list(range(2000,2021))

In [ ]:
lad_not_fd = uk_lad_not_fd.local_authority_code.unique().tolist()

In [ ]:
idxx = pd.MultiIndex.from_product([lad_not_fd,vehs,yrrs], names = ["local_authority_code", "vehicles", "year"])

In [ ]:
dff = pd.DataFrame(index = idxx).reset_index()

In [ ]:
dff["traffic_volume"] = 0.0

In [ ]:
dff.shape

(59682, 4)

In [ ]:
uk_lad_not_fd =  pd.merge(uk_lad_not_fd, dff, on="local_authority_code")

In [ ]:
uk_lad_not_fd.shape

(59682, 9)

In [ ]:
vehs

['Pedal Cycles',
 'Motor Cycles',
 'Cars and Taxis',
 'Buses and Coaches',
 'Lorries and Vans',
 '2 rigid axle HGV',
 '3 rigid axle HGV',
 '3/4 rigid axle HGV',
 '4 rigid axle HGV',
 '5 articulated axle HGV',
 '6 articulated axle HGV',
 'Heavy Goods Vehicles',
 'Motor vehicles',
 'All vehicles']

In [ ]:
df_lists = [uk_lad_not_fd[uk_lad_not_fd["vehicles"] == v].reset_index(drop=True) for v in vehs]

In [ ]:
for df, (minn,maxx) in zip(df_lists, all_min_max_vals):
  df["traffic_volume"] = random.sample(list(np.linspace(round(minn),round(maxx), num=df.shape[0])), df.shape[0])

In [ ]:
df_lad_not_fd = pd.concat(df_lists, ignore_index=True)

In [ ]:
df_lad_not_fd

id local_authority_code LAD13CDO            LAD13NM LAD13NMW  \
0      E07000004            E07000004     11UB     Aylesbury Vale     None   
1      E07000004            E07000004     11UB     Aylesbury Vale     None   
2      E07000004            E07000004     11UB     Aylesbury Vale     None   
3      E07000004            E07000004     11UB     Aylesbury Vale     None   
4      E07000004            E07000004     11UB     Aylesbury Vale     None   
...          ...                  ...      ...                ...      ...   
59677  S12000024            S12000024     00RB  Perth and Kinross     None   
59678  S12000024            S12000024     00RB  Perth and Kinross     None   
59679  S12000024            S12000024     00RB  Perth and Kinross     None   
59680  S12000024            S12000024     00RB  Perth and Kinross     None   
59681  S12000024            S12000024     00RB  Perth and Kinross     None   

                                                geometry      vehicles  year  \
0      POLYGON ((-0.87078 52.03998, -0.86973 52.03998...  Pedal Cycles  2000   
1      POLYGON ((-0.87078 52.03998, -0.86973 52.03998...  Pedal Cycles  2001   
2      POLYGON ((-0.87078 52.03998, -0.86973 52.03998...  Pedal Cycles  2002   
3      POLYGON ((-0.87078 52.03998, -0.86973 52.03998...  Pedal Cycles  2003   
4      POLYGON ((-0.87078 52.03998, -0.86973 52.03998...  Pedal Cycles  2004   
...                                                  ...           ...   ...   
59677  MULTIPOLYGON (((-3.26286 56.35524, -3.26703 56...  All vehicles  2016   
59678  MULTIPOLYGON (((-3.26286 56.35524, -3.26703 56...  All vehicles  2017   
59679  MULTIPOLYGON (((-3.26286 56.35524, -3.26703 56...  All vehicles  2018   
59680  MULTIPOLYGON (((-3.26286 56.35524, -3.26703 56...  All vehicles  2019   
59681  MULTIPOLYGON (((-3.26286 56.35524, -3.26703 56...  All vehicles  2020   

       traffic_volume  
0        1.830488e+06  
1        9.732486e+05  
2        1.746799e+06  
3        1.825113e+06  
4        7.383044e+05  
...               ...  
59677    7.271466e+08  
59678    7.498411e+08  
59679    5.865794e+08  
59680    6.651997e+08  
59681    3.313815e+08  

[59682 rows x 9 columns]

In [ ]:
len(df_lad_not_fd["id"].unique().tolist())

203

In [ ]:
df_uk_lad_geojson_agg = pd.concat([df_lad_not_fd, uk_lad_geojson_agg], ignore_index=True)

In [ ]:
# df_ped["traffic_volume"] = random.sample(list(np.linspace(round(pedal_min),round(pedal_max), num=pedal_size)), pedal_size)

In [ ]:
df_uk_lad_geojson_agg.shape

(111160, 9)

In [ ]:
# uk_lad_not_fd["rand"] = random.sample(list(range(250,1000)), uk_lad_not_fd.shape[0])

In [ ]:
# ct = 0
# for idx in lad_code:
#   if idx not in uk_lad_geojson["id"].unique().tolist():
#     ct += 1
#     print(idx, ct)

In [ ]:
##aggreate volume of traffic by lad code
uk_region_traffic_volume = uk_traffic.groupby(["year", "vehicles", 'region_name'], as_index=False).agg(traffic_volume =("vehicles_miles_driven", sum))

In [ ]:
uk_traffic.region_name.unique()

array(['North West', 'Scotland', 'South East', 'Wales',
       'Yorkshire & Humber', 'East of England', 'West Midlands',
       'East Midlands', 'South West', 'North East', 'London'],
      dtype=object)

In [ ]:
uk_geojson["EER13NM"].replace({"Yorkshire and The Humber": "Yorkshire & Humber", "Eastern": "East of England"}, inplace=True)

In [ ]:
uk_geojson.rename({"EER13NM": 'region_name'}, axis=1, inplace=True)

In [ ]:
df_uk_geojson = pd.merge(uk_geojson, uk_region_traffic_volume, on="region_name")

In [ ]:
df_uk_geojson.head()

id    EER13CD EER13CDO region_name  \
0  E15000001  E15000001       01  North East   
1  E15000001  E15000001       01  North East   
2  E15000001  E15000001       01  North East   
3  E15000001  E15000001       01  North East   
4  E15000001  E15000001       01  North East   

                                            geometry  year  \
0  MULTIPOLYGON (((-1.22485 54.62540, -1.22381 54...  2000   
1  MULTIPOLYGON (((-1.22485 54.62540, -1.22381 54...  2000   
2  MULTIPOLYGON (((-1.22485 54.62540, -1.22381 54...  2000   
3  MULTIPOLYGON (((-1.22485 54.62540, -1.22381 54...  2000   
4  MULTIPOLYGON (((-1.22485 54.62540, -1.22381 54...  2000   

                 vehicles  traffic_volume  
0        2 rigid axle HGV    1.778347e+08  
1        3 rigid axle HGV    2.889599e+07  
2      3/4 rigid axle HGV    3.886851e+07  
3        4 rigid axle HGV    3.135521e+07  
4  5 articulated axle HGV    9.534821e+07

In [ ]:
mapbox_token = "pk.eyJ1IjoiYWRlYm95ZWEiLCJhIjoiY2wwaWpjcW0wMDM3azNibGdhbTRubXB3ayJ9.6UyFRoMwp6XytQwQua-9WA"

In [ ]:
# for feature in counties['features']:
#     print(feature['id'])

In [ ]:
os.listdir()

['dft_traffic_counts_aadf.csv',
 'uk_shape_file',
 'uk_road_map.geojson',
 'ne_50m_rivers_lake_centerlines.zip',
 'uk_traffic_analysis.ipynb',
 'assets']

In [ ]:
# #save geo dataframe as parquet
# df_uk_geojson.to_parquet('uk_shape_file/uk_geojson_agg.parquet') 
# df_uk_lad_geojson_agg.to_parquet('uk_shape_file/uk_lad_geojson_agg.parquet')

In [ ]:
# df_uk_geojson.to_file("uk_shape_file/uk_geojson_agg.geojson", driver='GeoJSON')
# df_uk_lad_geojson_agg.to_file("uk_shape_file/uk_lad_geojson_agg.geojson", driver='GeoJSON')

In [ ]:
df_uk_geojson_pq = gpd.read_parquet('uk_shape_file/uk_geojson_agg.parquet')
df_uk_lad_geojson_pq = gpd.read_parquet('uk_shape_file/uk_lad_geojson_agg.parquet')

In [ ]:
# df_uk_geojson_pq

In [ ]:
px.set_mapbox_access_token(mapbox_token)

In [ ]:
df_mtr_uk = df_uk_geojson_pq[(df_uk_geojson_pq["year"] == 2000) & (df_uk_geojson_pq["vehicles"] == 'All vehicles')].copy()

In [ ]:
fig = go.Figure(go.Choroplethmapbox(geojson=data, locations=df_mtr_uk.id, featureidkey="properties.id", z=df_mtr_uk.traffic_volume,
                                    colorscale="YlOrRd",
                                    colorbar=dict(thickness=30, ticklen=3, x=0.85,len=0.7,
                                                  title=dict(
                                                      text="Volume of traffic",
                                                      font={"color": "#ffffff", "family": "Cambria", "size":16},
                                                      ),
                                                  ticks="outside",
                                                  tickfont={"family": "Cambria", "color": "#ffffff", "size":16}
                                                  ),
                                    # coloraxis='coloraxis',
                                    text=df_mtr_uk.region_name,
                                    hovertemplate = 
                                    '<br><b>Miles travelled</b>: %{z:.0f}<br>'+
                                    '<b>Region</b>: %{text}<extra></extra>',
                                    marker_opacity=0.95))
fig.update_layout(
    margin={"r":0,"t":0,"l":0,"b":0},
    mapbox_style='carto-darkmatter',
    mapbox_zoom=4.5, mapbox_center = {"lat": 54.55, "lon":-2.20},
    width=1400,
    height=700,)
fig.update_traces(showscale=True)
fig.show()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
# fig = px.choropleth_mapbox(df_mtr_uk, geojson=data, locations="id", featureidkey="properties.id", color='traffic_volume',
#                            color_continuous_scale="YlOrRd",
#                            mapbox_style='carto-darkmatter',
#                            center={"lat": 54.55, "lon":-2.20},
#                            hover_name = "region_name",
#                            hover_data={"id":False,
#                                        "region_name":True},
#                            zoom=4.5,
#                            opacity=1,
#                            labels={'traffic_volume':'Volume of traffic',
#                                    "region_name": 'Region'},
#                           )
# fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0},
#                   template="plotly_dark",
#                   width=1200,
#                   height=700,
#                   legend=dict(
#                       bgcolor = 'rgba(0,0,0,0)',
#                       orientation = 'h', y=1, 
#                       yanchor="bottom", x=0.5, xanchor="center"),
#                   mapbox_accesstoken=mapbox_token)
# fig.show()

In [ ]:
# for idx, feature in enumerate(counties['features']):
#   print(idx, feature['id'])

In [ ]:
df_mtr_lad_uk = df_uk_lad_geojson_pq[(df_uk_lad_geojson_pq["year"] == 2010) & (df_uk_lad_geojson_pq["vehicles"] == 'Cars and Taxis')].copy()

In [ ]:
len(df_mtr_lad_uk.id.unique())

380

In [ ]:
# fig = px.choropleth_mapbox(df_mtr_lad_uk, geojson=lad_data, locations="id", featureidkey="properties.id", color='traffic_volume',
#                            color_continuous_scale="YlOrRd",
#                            mapbox_style='carto-darkmatter',
#                            center={"lat": 54.55, "lon":-2.20},
#                            hover_name = "LAD13NM",
#                            hover_data={"id":False,
#                                        "LAD13NM":True},
#                            zoom=4.5,
#                            opacity=1,
#                            labels={'traffic_volume':'Volume of traffic',
#                                    "LAD13NM": 'Local Authority'},
#                           )
# fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0},
#                   mapbox_accesstoken=mapbox_token)
# fig.show()

In [ ]:
fig = go.Figure(go.Choroplethmapbox(geojson=lad_data, locations=df_mtr_lad_uk.id, featureidkey="properties.id", z=df_mtr_lad_uk.traffic_volume,
                                    colorscale="YlOrRd",
                                    colorbar=dict(thickness=30, ticklen=3, x=0.85,len=0.7,
                                                  title=dict(
                                                      text="Volume of traffic",
                                                      font={"color": "#ffffff", "family": "Cambria", "size":16},
                                                      ),
                                                  ticks="outside",
                                                  tickfont={"family": "Cambria", "color": "#ffffff", "size":16}
                                                  ),
                                    # coloraxis='coloraxis',
                                    text=df_mtr_lad_uk.LAD13NM,
                                    hovertemplate = 
                                    '<br><b>Miles travelled</b>: %{z:.0f}<br>'+
                                    '<b>Local Authority</b>: %{text}<extra></extra>',
                                    marker_opacity=0.9))
fig.update_layout(
    margin={"r":120,"t":0,"l":120,"b":0},
    mapbox_style='carto-darkmatter',
    mapbox_zoom=4.5, mapbox_center = {"lat": 54.55, "lon":-2.20})
fig.update_traces(showscale=True)
fig.show()

Output hidden; open in https://colab.research.google.com to view.

#### replace local authority names in geojson with a single local authority name from the uk_traffic dataframe

In [ ]:
#Cambridgeshire
locals = [{"Cambridgeshire": ["East Cambridgeshire", "South Cambridgeshire", "Fenland", "Cambridge", "Huntingdonshire"]},
       {"Cumbria": ["Carlisle", "South Lakeland", "Allerdale", "Copeland", "Barrow-in-Furness", "Eden"]},
       {"Derbyshire": ["Chesterfield", "High Peak", "Amber Valley", "Derbyshire Dales", "North East Derbyshire", 
                     "Bolsover", "Erewash", "South Derbyshire"]},
       {"Devon": ["East Devon", "North Devon", "Exeter", "Torridge", "South Hams", "West Devon", "North Dorset",
                    "Mid Devon", "Teignbridge"]},
       {"Dorset": ["East Dorset", "West Dorset"]},
       {"East Sussex": ["Hastings", "Lewes", "Wealden", "Eastbourne", "Rother"]},
       {"Essex": ["Brentwood", "Colchester", "Maldon", "Basildon", "Uttlesford", "Castle Point", "Epping Forest",
                    "Rochford", "Braintree", "Chelmsford", "Harlow", "Tendring"]},
       {"Gloucestershire": ["Forest of Dean", "Cheltenham", "Tewkesbury", "Gloucester", "Cotswold", "Stroud"]},
       {"Hampshire": ["Eastleigh", "Hart", "Basingstoke and Deane", "Rushmoor", "Fareham", 
                          "Havant", "Test Valley", "East Hampshire", "Gosport", "New Forest", "Winchester"]},
       {"Kent": ["Ashford", "Dover", "Sevenoaks", "Canterbury", "Thanet", "Gravesham", "Tonbridge and Malling",
                     "Dartford", "Maidstone", "Swale", "Tunbridge Wells"]},
       {"Lancashire": ["Burnley", "Hyndburn", "Preston", "South Ribble", "Chorley", "Lancaster", "Ribble Valley",
                      "West Lancashire", "Fylde", "Pendle", "Rossendale", "Wyre"]},
       {"Leicestershire": ["Blaby", "Hinckley and Bosworth", "Charnwood", "Oadby and Wigston", "Melton",
                      "Harborough", "North West Leicestershire"]},
       {"Lincolnshire": ["Lincoln", "South Kesteven", "Boston", "North Kesteven", "West Lindsey", "East Lindsey", 
                     "South Holland"]},
       {"Norfolk": ["Broadland", "North Norfolk", "Great Yarmouth", "Norwich", "Breckland", "King's Lynn and West Norfolk", "South Norfolk"]},
       {"Northamptonshire": ["Corby", "Kettering", "Wellingborough", "Daventry", "Northampton", "East Northamptonshire", 
                      "South Northamptonshire"]},
       {"North Yorkshire": ["Harrogate", "Scarborough", "Craven", "Richmondshire", "Selby", "Hambleton", "Ryedale"]},
       {"Nottinghamshire": ["Bassetlaw", "Mansfield", "Broxtowe", "Newark and Sherwood", "Ashfield", "Gedling", 
                     "Rushcliffe"]},
       {"Oxfordshire": ["Cherwell", "Vale of White Horse", "Oxford", "West Oxfordshire", "South Oxfordshire"]},
       {"Somerset": ["Sedgemoor", "West Somerset", "South Somerset", "Mendip", "Taunton Deane"]},
       {"Staffordshire": ["Lichfield", "Stafford", "Cannock Chase", "Newcastle-under-Lyme", "Staffordshire Moorlands",
                      "East Staffordshire", "South Staffordshire", "Tamworth"]},
       {"Suffolk": ["Babergh", "Mid Suffolk", "Ipswich", "Suffolk Coastal"]},
       {"Surrey": ["Waveney", "Guildford", "Runnymede", "Tandridge", "Elmbridge", "Mole Valley", "Spelthorne",
                     "Waverley", "Epsom and Ewell", "Reigate and Banstead", "Surrey Heath", "Woking"]},
       {"Warwickshire": ["North Warwickshire", "Stratford-on-Avon", "Nuneaton and Bedworth", "Warwick", "Rugby"]},
       {"West Sussex": ["Arun", "Horsham", "Chichester", "Mid Sussex", "Adur", "Crawley", "Worthing"]},
       {"Worcestershire": ["Bromsgrove", "Worcester", "Malvern Hills", "Wychavon", "Redditch", "Wyre Forest"]},
       {"Hertfordshire": ["St Albans", "Stevenage", "Welwyn Hatfield", "East Hertfordshire", "Three Rivers",
                     "North Hertfordshire", "Watford", "Broxbourne", "Dacorum", "Hertsmere"]},
       {"Perth & Kinross": ["Perth and Kinross"]},
       {"Rhondda, Cynon, Taff": ["Rhondda Cynon Taf"]},
       {"East Cheshire": ["Cheshire East"]},
       {"Dumfries & Galloway": ["Dumfries and Galloway"]},
       {"Argyll & Bute": ["Argyll and Bute"]},
       {"West Cheshire": ["Cheshire West and Chester"]},
       {"Bournemouth": ["Christchurch"]},
       {"The Vale of Glamorgan": ["Vale of Glamorgan"]},
       {"Durham": ["County Durham"]},
       {"Cornwall excluding Isles of Scilly": ["Cornwall"]}]

In [ ]:
uk_lad_geojson_cpy = uk_lad_geojson.copy()

In [ ]:
for dct in locals:
  for key,val in dct.items():
    uk_lad_geojson_cpy['LAD13NM'] = uk_lad_geojson_cpy['LAD13NM'].replace(val, key)

In [ ]:
uk_lad_geojson_cpy.columns

Index(['id', 'LAD13CD', 'LAD13CDO', 'LAD13NM', 'LAD13NMW', 'geometry'], dtype='object')

In [ ]:
uk_lad_agg = uk_traffic.groupby(["region_name", "local_authority_name", "year", "vehicles"], as_index=False).agg(traffic_volume =("vehicles_miles_driven", sum))

In [ ]:
uk_lad_agg.rename({"local_authority_name": 'LAD13NM'}, axis=1, inplace=True)

In [ ]:
uk_lad_agg_geojson = pd.merge(uk_lad_geojson_cpy,uk_lad_agg, on='LAD13NM')

In [ ]:
uk_lad_agg_geojson.region_name.unique()

array(['North East', 'North West', 'Yorkshire & Humber', 'East Midlands',
       'West Midlands', 'South West', 'East of England', 'South East',
       'London', 'Scotland', 'Wales'], dtype=object)

In [ ]:
#save lad agg 
# uk_lad_agg_geojson.to_parquet('uk_shape_file/uk_lad_geojson_agg.parquet')

In [ ]:
df_mtr_lad_uk = uk_lad_agg_geojson[(uk_lad_agg_geojson["year"] == 2020) & (uk_lad_agg_geojson["vehicles"] == 'Heavy Goods Vehicles')].copy()

In [ ]:
fig = go.Figure(go.Choroplethmapbox(geojson=lad_data, locations=df_mtr_lad_uk.id, featureidkey="properties.id", z=df_mtr_lad_uk.traffic_volume,
                                    colorscale="YlOrRd",
                                    colorbar=dict(thickness=30, ticklen=3, x=0.85,len=0.7,
                                                  title=dict(
                                                      text="Volume of traffic",
                                                      font={"color": "#ffffff", "family": "Cambria", "size":16},
                                                      ),
                                                  ticks="outside",
                                                  tickfont={"family": "Cambria", "color": "#ffffff", "size":16}
                                                  ),
                                    # coloraxis='coloraxis',
                                    text=df_mtr_lad_uk.LAD13NM,
                                    hovertemplate = 
                                    '<br><b>Miles travelled</b>: %{z:.0f}<br>'+
                                    '<b>Local Authority</b>: %{text}<extra></extra>',
                                    marker_opacity=0.9))
fig.update_layout(
    margin={"r":120,"t":0,"l":120,"b":0},
    mapbox_style='carto-darkmatter',
    mapbox_zoom=4.5, mapbox_center = {"lat": 54.55, "lon":-2.20})
fig.update_traces(showscale=True)
fig.show()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
uk_lond_geojson = uk_lad_agg_geojson[(uk_lad_agg_geojson["region_name"] == 'London') & (uk_lad_agg_geojson["year"] == 2000) &
                   (uk_lad_agg_geojson["vehicles"] == "Heavy Goods Vehicles")]

In [ ]:
uk_traffic[(uk_traffic["region_name"] == 'East Midlands')]["latitude"].mean()

52.85639683897508

In [ ]:
lad_lat_cen = uk_traffic[uk_traffic["region_name"] == 'London']["latitude"].mean()
lad_long_cen = uk_traffic[uk_traffic["region_name"] == 'London']["longitude"].mean()

In [ ]:
fig = px.choropleth_mapbox(uk_lond_geojson, geojson=lad_data, locations="id", featureidkey="properties.id", color='traffic_volume',
                           color_continuous_scale="YlOrRd",
                           mapbox_style='carto-darkmatter',
                           center={"lat": lad_lat_cen, "lon":lad_long_cen},
                           hover_name = "LAD13NM",
                           hover_data={"id":False,
                                       "LAD13NM":True},
                           zoom=9.35,
                           opacity=0.8,
                           labels={'traffic_volume':'Volume of Traffic',
                                   "LAD13NM": 'Local Authority'},
                          )
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0},
                  mapbox_accesstoken=mapbox_token)
fig.show()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
fig = go.Figure(go.Choroplethmapbox(geojson=lad_data, locations=uk_lond_geojson.id, featureidkey="properties.id", z=uk_lond_geojson.traffic_volume,
                                    colorscale="YlOrRd",
                                    colorbar=dict(thickness=30, ticklen=3, x=0.85,len=0.7,
                                                  title=dict(
                                                      text="Volume of traffic",
                                                      font={"color": "#ffffff", "family": "Cambria", "size":16},
                                                      ),
                                                  ticks="outside",
                                                  tickfont={"family": "Cambria", "color": "#ffffff", "size":16}
                                                  ),
                                    # coloraxis='coloraxis',
                                    text=uk_lond_geojson.LAD13NM,
                                    hovertemplate = 
                                    '<br><b>Miles travelled</b>: %{z:.0f}<br>'+
                                    '<b>Local Authority</b>: %{text}<extra></extra>',
                                    marker_opacity=0.8))
fig.update_layout(
    margin={"r":120,"t":0,"l":120,"b":0},
    mapbox_style='carto-darkmatter',
    mapbox_zoom=9.3, mapbox_center = {"lat": lad_lat_cen, "lon":lad_long_cen})
fig.update_traces(showscale=True)
fig.show()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
# uk_shp = "uk_shape_file/2018-MRDB-minimal.shp"

In [ ]:
# print(gpd.read_file(uk_shp).crs) #epsg:27700

epsg:27700


In [ ]:
# uk_shp_map = gpd.read_file(uk_shp)

In [ ]:
# uk_shp_map.to_file('uk_road_map.geojson', driver='GeoJSON')

In [ ]:
uk_rd_shp_file = "uk_road_map.geojson"

In [ ]:
with open(uk_rd_shp_file) as f:
    uk_road_data = json.load(f)

In [ ]:
uk_road_data['features'][0].keys()

dict_keys(['type', 'properties', 'geometry'])

In [ ]:
uk_road_geojson = gpd.read_file(uk_rd_shp_file)

In [ ]:
# uk_road_geojson["rand"] = random.sample(list(range(2500,1000000)), uk_road_geojson.shape[0])

In [ ]:
# uk_road_geojson

In [ ]:
len(uk_road_geojson.RoadNumber.unique().tolist())

1838

In [ ]:
rd_nums = uk_road_geojson.RoadNumber.unique().tolist()

In [ ]:
rd_names = uk_traffic.road_name.unique().tolist()

In [ ]:
rds = [ rd for rd in rd_nums if rd in rd_names]

In [ ]:
lats = []
lons = []
names = []
ct = 0

for feature, name in zip(uk_road_geojson.geometry, uk_road_geojson.RoadNumber):
  ct += 1
  if isinstance(feature, shapely.geometry.linestring.LineString):
    linestrings = [feature]
    # print(linestrings)
  for linestring in linestrings:
    x, y = linestring.xy
    lats = np.append(lats, y)
    lons = np.append(lons, x)
    names = np.append(names, [name]*len(y))
    lats = np.append(lats, None)
    lons = np.append(lons, None)
    names = np.append(names, None)

In [ ]:
latid, longid = [],[]

In [ ]:
transformer = Transformer.from_crs("epsg:27700", "epsg:4326")

for y,x in zip(lats,lons):
  if y and x:
    x1,y1 = transformer.transform(x, y)
  else:
    x1,y1 = x,y
  longid.append(y1)
  latid.append(x1)

In [ ]:
def convert_roadlines_wgs84(df):

  lats = []
  lons = []
  names = []

  for feature, name in zip(df.geometry, df.RoadNumber):
    if isinstance(feature, shapely.geometry.linestring.LineString):
      linestrings = [feature]
      # print(linestrings)
    for linestring in linestrings:
      x, y = linestring.xy
      lats = np.append(lats, y)
      lons = np.append(lons, x)
      names = np.append(names, [name]*len(y))
      lats = np.append(lats, None)
      lons = np.append(lons, None)
      names = np.append(names, None)

  lati, longi = [],[]
  transformer = Transformer.from_crs("epsg:27700", "epsg:4326")

  for y,x in zip(lats,lons):
    if y and x:
      x1,y1 = transformer.transform(x, y)
    else:
      x1,y1 = x,y
    longi.append(y1)
    lati.append(x1)

  return lati,longi,names

In [ ]:
latid,longid,names = convert_roadlines_wgs84(uk_road_geojson)

In [ ]:
len(names)

54579

In [ ]:
df_road_geojson = pd.DataFrame(list(zip(latid, longid, names)), 
                               columns=['latitude','longitude', 'road_number'])

In [ ]:
df_road_geojson.shape

(54579, 3)

In [ ]:
df_road_geojson.to_csv("road_geojson.csv", index=False)

In [ ]:
df_road_geojson = pd.read_csv("road_geojson.csv")

In [ ]:
df_busy_rd = uk_road_geojson[uk_road_geojson["RoadNumber"].isin(busiest_roads)].copy()

In [ ]:
bs_latid, bs_longid, bs_names = convert_roadlines_wgs84(df_busy_rd)

In [ ]:
uk_rd_traffic_volume = uk_traffic.groupby(["road_name"], as_index=False).agg(traffic_volume =("vehicles_miles_driven", sum))

In [ ]:
uk_rd_traffic_volume = uk_rd_traffic_volume.sort_values(by=['traffic_volume'], ascending=False).reset_index(drop=True)

In [ ]:
top10_rds = uk_rd_traffic_volume.road_name[:10].values.tolist()
top50_rds = uk_rd_traffic_volume.road_name[:50].values.tolist()
top100_rds = uk_rd_traffic_volume.road_name[:100].values.tolist()

In [ ]:
df_top10_rd = uk_road_geojson[uk_road_geojson["RoadNumber"].isin(top10_rds)].copy()
df_top50_rd = uk_road_geojson[uk_road_geojson["RoadNumber"].isin(top50_rds)].copy()
df_top100_rd = uk_road_geojson[uk_road_geojson["RoadNumber"].isin(top100_rds)].copy()

In [ ]:
top10_latid, top10_longid, top10_names = convert_roadlines_wgs84(df_top10_rd)
top50_latid, top50_longid, top50_names = convert_roadlines_wgs84(df_top50_rd)
top100_latid, top100_longid, top100_names = convert_roadlines_wgs84(df_top100_rd)

In [ ]:
df_road_top10 = pd.DataFrame(list(zip(top10_latid, top10_longid, top10_names)), 
                               columns=['latitude','longitude', 'road_number'])
df_road_top50 = pd.DataFrame(list(zip(top50_latid, top50_longid, top50_names)), 
                               columns=['latitude','longitude', 'road_number'])
df_road_top100 = pd.DataFrame(list(zip(top100_latid, top100_longid, top100_names)), 
                               columns=['latitude','longitude', 'road_number'])

In [ ]:
df_road_top10.to_csv("road10_geojson.csv", index=False)
df_road_top50.to_csv("road50_geojson.csv", index=False)
df_road_top100.to_csv("road100_geojson.csv", index=False)

NameError: ignored

In [ ]:
# fig = px.line_mapbox(df_road_geojson, lat='latitude', lon='longitude')

# fig.update_layout(
#     margin={"r":0,"t":0,"l":0,"b":0},
#     mapbox=go.layout.Mapbox(
#         style='carto-darkmatter',
#         zoom=4.5, 
#         center_lat = 54.5,
#         center_lon = -2.24,
#     )
# )
# fig.show()


In [ ]:
busiest_roads

['M1', 'M6', 'M4', 'M25', 'A1', 'M5', 'M62', 'M40', 'A38', 'A14']

In [ ]:
uk_road_data["features"][0]["type"]

'Feature'

In [ ]:
# transformer = Transformer.from_crs("epsg:27700", "epsg:4326")
# for idx, feature in enumerate(uk_road_data['features']):
#     if feature['geometry']['type'] == 'LineString':
#         # all coordinates
#         coords = feature['geometry']['coordinates']
#         print(coords)
#         # coordList is for each individual polygon
#         for coordList in coords:
#             lat_grid, lng_grid = coordList
#             # do transformation
#             # coordList[0],coordList[1] = pyproj.transform(InputGrid, wgs84, lat_grid, lng_grid) # methode 1
#             coordList[0],coordList[1] = transformer.transform(lat_grid, lng_grid) # methode 2
#         #     coords.append(coordList)
#         # feature["geometry"]["coords"] = coords
#         print(feature['geometry']['coordinates'])
#         # if idx == 10:
#         #   break

In [ ]:
# fig = go.Figure(
#     go.Scattermapbox(),
#     layout = {
#         'mapbox': {
#             'style': "stamen-terrain",
#             'zoom': 10
#         },
#         'margin': {'l':0, 'r':0, 'b':0, 't':0},
#     }
# )

# fig.update_mapboxes(layers=[
#     {
#         'source': feature, 
#         'type': "line", 
#         'line': {'width': 5},
#         'below': "traces", 
#         'color': "royalblue"
#     } for feature in uk_road_data["features"]])

# fig.update_layout(
#     margin={"r":0,"t":0,"l":0,"b":0},
#     mapbox=go.layout.Mapbox(
#         style="stamen-terrain", 
#         zoom=4.5, 
#         center_lat = 54.5,
#         center_lon = -2.24,
#     )
# )
# fig.show()

In [ ]:
##latitude -> np.array(feature["geometry"]["coordinates"])[:,1]
##longitude -> np.array(feature["geometry"]["coordinates"])[:,0]

In [ ]:
# for idx, feature in enumerate(uk_road_data['features']):
#   print(np.array(feature["geometry"]["coordinates"]))
#   #print(np.array(feature["geometry"]["coords"])[:,0])
#   if idx == 10:
#     break

In [ ]:
# ct = 0
# for i in range(0,len(longid)-2,3):
#   ct += 1
#   print(i, longid[i],longid[i+1])
#   print(names[i])

In [ ]:
# fig = px.scatter_mapbox(lat=[for v in latid if ], lon=longid,color=names, size=rand_vals,
#                   color_continuous_scale=px.colors.cyclical.IceFire, size_max=15, zoom=10)

# fig.update_layout(
#     margin={"r":0,"t":0,"l":0,"b":0},
#     mapbox=go.layout.Mapbox(
#         style='carto-darkmatter', 
#         zoom=4.5, 
#         center_lat = 54.5,
#         center_lon = -2.24,
#         accesstoken=mapbox_token
#     )
# )
# fig.show()

In [ ]:
road_dct = {"all":df_road_geojson}

In [ ]:
sel = "all"

In [ ]:
fig = go.Figure(
        go.Scattermapbox(
            lat=df_road_geojson.latitude.values.tolist(),
            lon=df_road_geojson.longitude.values.tolist(),
            mode="markers+lines",
            line=dict(width=1, color='crimson'),
            marker=dict(
                size= (1.75 if sel == "all" else 2.5),
                color = 'gold',
                opacity = .8,
            ),
            text=df_road_geojson.road_number.values.tolist(),
            hovertemplate =
            '<b>Latitude</b>: %{lat:.2f}'+
            '<br><b>Longitude</b>: %{lon:.2f}<br>'+
            '<b>Road number</b>: %{text}<extra></extra>',
            opacity=0.4,
        )
)

fig.update_layout(
    margin={"r":0,"t":15,"l":0,"b":0},
    mapbox=go.layout.Mapbox(
        style= "carto-darkmatter", #"mapbox://styles/shaz13/cjiog1iqa1vkd2soeu5eocy4i", #carto-darkmatter
        zoom=4.5, 
        center_lat = 54.5,
        center_lon = -2.24,
        accesstoken=mapbox_token,
        # bearing=10,
        # pitch=60,
    ),
    width=1100,
    height=700, 
)
fig.show()

In [ ]:
fig = go.Figure(
        go.Scattermapbox(
            lat=df_road_top50.latitude.values.tolist(), 
            lon=df_road_top50.longitude.values.tolist(),
            mode="markers+lines",
            line=dict(width=3, color='crimson'),
            marker=dict(
                size= 2.5,
                color = 'gold',
                opacity = .8,
            ),
            text=df_road_top50.road_number.values.tolist(),
            hovertemplate =
            '<b>Latitude</b>: %{lat:.2f}'+
            '<br><b>Longitude</b>: %{lon:.2f}<br>'+
            '<b>Road number</b>: %{text}<extra></extra>',
            opacity=0.4,
        )
)

fig.update_layout(
    margin={"r":0,"t":15,"l":0,"b":0},
    mapbox=go.layout.Mapbox(
        style= "carto-darkmatter", #"mapbox://styles/shaz13/cjiog1iqa1vkd2soeu5eocy4i", #carto-darkmatter
        zoom=4.5, 
        center_lat = 54.5,
        center_lon = -2.24,
        accesstoken=mapbox_token,
        # bearing=10,
        # pitch=60,
    ),
    width=1100,
    height=700, 
)
fig.show()

In [ ]:
df_uk_aadf = uk_traffic[["latitude", "longitude", "year", "region_name", "vehicles", "vehicles_aadf"]].copy()

In [ ]:
# df_uk_aadf[(df_uk_aadf["vehicles"] == "all_vehicles") & (df_uk_aadf["year"] == 2020) & (df_uk_aadf["region_name"] == "London")]
df_uk_aadf.shape

(5269474, 6)

In [ ]:
df_uk_aadf.to_parquet('df_uk_aadf.parquet.gzip', compression='gzip')

In [ ]:
df_uk_aadf = pd.read_parquet('df_uk_aadf.parquet.gzip')

In [ ]:
df_uk_aadf["vehicles"].unique()

array(['Pedal Cycles', 'Motor Cycles', 'Cars and Taxis',
       'Buses and Coaches', 'Lorries and Vans', '2 rigid axle HGV',
       '3 rigid axle HGV', '3/4 rigid axle HGV', '4 rigid axle HGV',
       '5 articulated axle HGV', '6 articulated axle HGV',
       'Heavy Goods Vehicles', 'Motor vehicles', 'All vehicles'],
      dtype=object)

In [ ]:
df_uk_aadf[(df_uk_aadf["vehicles"] == 'Motor vehicles') & (df_uk_aadf["year"] == 2020)].vehicles_aadf.max()

187021

In [ ]:
df_allvehs_aadf = df_uk_aadf[(df_uk_aadf["vehicles"] == "All vehicles") & (df_uk_aadf["year"] == 2010)].copy()

In [ ]:
df_allvehs_aadf.columns

Index(['latitude', 'longitude', 'year', 'region_name', 'vehicles',
       'vehicles_aadf'],
      dtype='object')

In [ ]:
fig = go.Figure(go.Densitymapbox(lat=df_allvehs_aadf.latitude, lon=df_allvehs_aadf.longitude, z=df_allvehs_aadf.vehicles_aadf,
                                 radius=5, colorscale="Blackbody_r", 
                                 colorbar=dict(thickness=30, ticklen=3, x=0.85,len=0.7,
                                               title=dict(
                                                   text="Annual Average Daily Flow",
                                                   font={"color": "#ffffff", "family": "Cambria", "size":16},
                                                   ),
                                               ticks="outside",
                                               tickfont={"family": "Cambria", "color": "#ffffff", "size":16}
                                               ),
                                 text=df_allvehs_aadf.region_name,
                                 hovertemplate = 
                                 '<br><b>Region</b>: %{text}<br>'+
                                 '<br><b>Annual Average Daily Flow</b>: %{z:.0f}<br><extra></extra>',
                                 opacity=0.8,
                                 showscale=True)
)
fig.add_trace(go.Scattermapbox(
            lat=latid,
            lon=longid,
            mode="lines",
            line=dict(width=0.75, color='darkcyan'),
            text=names,
            hovertemplate =
            '<b>Latitude</b>: %{lat:.2f}'+
            '<br><b>Longitude</b>: %{lon:.2f}<br>'+
            '<b>Road number</b>: %{text}<extra></extra>',
            opacity=0.25,
        ))
fig.update_layout(
    margin={"r":0,"t":0,"l":0,"b":0},
    mapbox_style='carto-darkmatter',
    mapbox_zoom=4.5, mapbox_center = {"lat": 54.55, "lon":-2.20},
    mapbox_accesstoken=mapbox_token)

fig.show()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
# fig = px.density_mapbox(df_uk_aadf[(df_uk_aadf["vehicles"] == "all_vehicles") & (df_uk_aadf["year"] == 2010)], lat='latitude', 
#                         lon='longitude', z='vehicles_aadf', radius=3,
#                         color_continuous_scale = "Blackbody_r",
#                         center={"lat": 54.55, "lon":-2.20}, 
#                         zoom=4.5,
#                         hover_data={"longitude":False,
#                                     "latitude":False,
#                                     },
#                         labels={'vehicles_aadf':'Annual Average Daily Flow',
#                                 },
#                         mapbox_style="carto-darkmatter")

# fig.add_trace(go.Scattermapbox(
#             lat=latid,
#             lon=longid,
#             mode="lines",
#             line=dict(width=0.75, color='darkcyan'),
#             text=names,
#             hovertemplate =
#             '<b>Latitude</b>: %{lat:.2f}'+
#             '<br><b>Longitude</b>: %{lon:.2f}<br>'+
#             '<b>Road number</b>: %{text}<extra></extra>',
#             opacity=0.2,
#         ))

# fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0},
#                   mapbox_accesstoken=mapbox_token)
# fig.show()

In [ ]:
# df_uk_aadf[(df_uk_aadf["vehicles"] == "all_vehicles") & (df_uk_aadf["year"] == 2020) & (df_uk_aadf["region_name"] == "London")]
lad_long_cen

-0.12921770965805576

In [ ]:
df_uk_aadf_reg = df_uk_aadf[(df_uk_aadf["vehicles"] == "All vehicles") & (df_uk_aadf["year"] == 2020) \
                                   & (df_uk_aadf["region_name"] == 'London')].copy()

In [ ]:
lad_lat_cen = df_uk_aadf[df_uk_aadf["region_name"] == 'London']["latitude"].mean()
lad_long_cen = df_uk_aadf[df_uk_aadf["region_name"] == 'London']["longitude"].mean()

In [ ]:
fig = go.Figure(go.Densitymapbox(lat=df_uk_aadf_reg.latitude, lon=df_uk_aadf_reg.longitude, z=df_uk_aadf_reg.vehicles_aadf,
                                 radius=25, colorscale="Blackbody_r", 
                                 colorbar=dict(thickness=30, ticklen=3, x=0.85,len=0.7,
                                               title=dict(
                                                   text="Annual Average Daily Flow",
                                                   font={"color": "#ffffff", "family": "Cambria", "size":16},
                                                   ),
                                               ticks="outside",
                                               tickfont={"family": "Cambria", "color": "#ffffff", "size":16}
                                               ),
                                 text=df_uk_aadf_reg.region_name,
                                 hovertemplate = 
                                 '<br><b>Region</b>: %{text}<br>'+
                                 '<br><b>Annual Average Daily Flow</b>: %{z:.0f}<br><extra></extra>',
                                 opacity=0.8,
                                 showscale=True)
)
fig.add_trace(go.Scattermapbox(
            lat=latid,
            lon=longid,
            mode="lines",
            line=dict(width=0.75, color='darkcyan'),
            text=names,
            hovertemplate =
            '<b>Latitude</b>: %{lat:.2f}'+
            '<br><b>Longitude</b>: %{lon:.2f}<br>'+
            '<b>Road number</b>: %{text}<extra></extra>',
            opacity=0.2,
        ))
fig.update_layout(
    margin={"r":0,"t":0,"l":0,"b":0},
    mapbox_style='carto-darkmatter',
    mapbox_zoom=9.3, mapbox_center = {"lat": lad_lat_cen, "lon":lad_long_cen},
    mapbox_accesstoken=mapbox_token)

fig.show()

In [ ]:
fig = px.density_mapbox(df_uk_aadf_reg, lat='latitude', 
                        lon='longitude', z='vehicles_aadf', radius=25,
                        color_continuous_scale = "Blackbody_r",
                        center={"lat": lad_lat_cen, "lon":lad_long_cen}, 
                        zoom=9.5,
                        hover_data={"longitude":False,
                                    "latitude":False,
                                    },
                        labels={'vehicles_aadf':'Annual Average Daily Flow',
                                },
                        mapbox_style="carto-darkmatter")

fig.add_trace(go.Scattermapbox(
            lat=latid,
            lon=longid,
            mode="lines",
            line=dict(width=0.5, color='darkcyan'),
            text=names,
            hovertemplate =
            '<b>Latitude</b>: %{lat:.2f}'+
            '<br><b>Longitude</b>: %{lon:.2f}<br>'+
            '<b>Road number</b>: %{text}<extra></extra>',
            opacity=0.6,
        ))

fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0},
                  mapbox_accesstoken=mapbox_token)
fig.show()

In [ ]:
# fig = px.choropleth_mapbox(uk_road_geojson, geojson=uk_road_data, locations="CP_Number", featureidkey="properties.CP_Number", color='rand',
#                            color_continuous_scale="Darkmint",
#                            mapbox_style='carto-positron',
#                            center={"lat": 54.55, "lon":-2.20},
#                            hover_name = "RoadNumber",
#                            hover_data={"CP_Number":False,
#                                        "RoadNumber":True},
#                            zoom=4.5,
#                            opacity=1,
#                            labels={'rand':'Land Mass',
#                                    "RoadNumber": 'Road Name'},
#                           )
# fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0},
#                   mapbox_accesstoken=mapbox_token)
# fig.show()

array(['A560', 'A905', 'M20', ..., 'M41', 'A2009', 'M6Toll'], dtype=object)